In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
%matplotlib inline

In [2]:
class NNModel:
    
    def __init__(self,learning_rate, n_iter, args):
        self.learning_rate = learning_rate
        self.args = args
        self.n_iter = n_iter
    
    def z_score(self,w,x,b):
        return np.dot(w,x)+b
    
    def init_params(self,n_x):
        parameters={}
        n_a = n_x
        for i in range(1,len(self.args)+1):
            n_h = self.args[i-1][0]
            parameters['w'+str(i)] = np.random.rand(n_h,n_a)*np.sqrt(1/n_x)
            parameters['b'+str(i)] = np.random.randn(n_h,1)
            n_a = n_h
        return parameters
    
    def activation(self,z,fn = 'linear'):
        act_fn ={'linear':z,
                 'relu':np.maximum(z,0),
                 'tanh':np.tanh(z),
                 'sigmoid':1/(1+np.exp(-z)),
                 'softmax':np.exp(z)/np.sum(np.exp(z))}
        return act_fn[fn]
    
    def forward_prop(self,x, parameters):
        L = len(args)
        z_scores = {}
        activations = {'a0':x}
        for i in range(1,L+1):
            z_scores['z'+str(i)] = self.z_score(parameters['w'+str(i)],activations['a'+str(i-1)],parameters['b'+str(i)])
            z = z_scores['z'+str(i)]
            activations['a'+str(i)] = self.activation(z,fn=self.args[i-1][1])
        
        return z_scores, activations
    
    def compute_cost(self,y,y_hat):
        m = y.shape[0]
        cost = (-1/m)*(np.dot(y, np.log(y_hat.T)) + np.dot(1-y, np.log(1-y_hat.T)))
        return np.squeeze(cost)
        
    def backprop(self,y, parameters, z_scores, activations):
        gradients = {}
        L = len(self.args)
        m = y.shape[0]
        for i in range(L,0,-1):
            if i==L:
                gradients['dz'+str(i)]=activations['a'+str(i)]-y
            else:
                gradients['dz'+str(i)] = np.multiply(np.dot(parameters['w'+str(i+1)].T, gradients['dz'+str(i+1)]), 1*(z_scores['z'+str(i)]>=0))
            dz = gradients['dz'+str(i)]
            gradients['dw'+str(i)] = (1/m)*np.matmul(dz,activations['a'+str(i-1)].T)
            gradients['db'+str(i)] = (1/m)*np.sum(dz,axis=1,keepdims=True)
        return gradients
    
    def update_params(self,parameters, gradients):
        eta = self.learning_rate
        for i in range(1,len(parameters)//2+1):
            parameters['w'+str(i)]-=eta*gradients['dw'+str(i)]
            parameters['b'+str(i)]-=eta*gradients['db'+str(i)]
        return parameters
    
    def fit(self,x,y):
        np.random.seed(5)
        params = self.init_params(x.shape[0])
        for i in range(self.n_iter):
            z_scores,activations = self.forward_prop(x,params)
            y_hat = activations['a'+str(len(self.args))]
            #print(y_hat)
            cost = self.compute_cost(y,y_hat)
            gradients = self.backprop(y,params,z_scores,activations)
            params = self.update_params(params,gradients)
            if i%1==0:
                print('Iteration : {}      Cost : {}'.format(i,cost))
        return params
    
    def predict(self,x_test,params):
        z_scores, activations = self.forward_prop(x_test,params)
        y_pred = 1*(activations['a'+str(len(params)//2)]>0)
        return np.squeeze(y_pred)

In [3]:
path = '/home/mrityunjay/Downloads/sonar.csv'
df = pd.read_csv(path)
df.columns=['x'+str(i) for i in range(len(df.columns))]

x = np.transpose(df.drop(['x60'],axis=1).values)
y = 1*(df['x60']=='R').values
y = y.reshape(y.shape[0],1).T

In [9]:
args=[(10,'relu'),(5,'relu'),(1,'sigmoid')]
x_test = np.random.randn(60,1)
nn = NNModel(learning_rate=0.0001, n_iter = 100000, args=args)
params = nn.fit(x,y)
y_pred = nn.predict(x_test,params)
print(y_pred)

Iteration : 0      Cost : 144.78082122426005
Iteration : 1      Cost : 144.66772436836732
Iteration : 2      Cost : 144.5658921277834
Iteration : 3      Cost : 144.47424078722054
Iteration : 4      Cost : 144.3917846795561
Iteration : 5      Cost : 144.31762808927567
Iteration : 6      Cost : 144.25095774343924
Iteration : 7      Cost : 144.19103585204485
Iteration : 8      Cost : 144.1371936631475
Iteration : 9      Cost : 144.08882550080253
Iteration : 10      Cost : 144.0453832560433
Iteration : 11      Cost : 144.00637130283917
Iteration : 12      Cost : 143.97134181242413
Iteration : 13      Cost : 143.9398904406452
Iteration : 14      Cost : 143.91165236410887
Iteration : 15      Cost : 143.88629864195997
Iteration : 16      Cost : 143.86353288113838
Iteration : 17      Cost : 143.84308818395337
Iteration : 18      Cost : 143.8247243577952
Iteration : 19      Cost : 143.8082253677884
Iteration : 20      Cost : 143.79339701416802
Iteration : 21      Cost : 143.7800648171417
Iterat

Iteration : 344      Cost : 143.4619411496687
Iteration : 345      Cost : 143.46136023195783
Iteration : 346      Cost : 143.46077970237496
Iteration : 347      Cost : 143.46019917704865
Iteration : 348      Cost : 143.45961823805027
Iteration : 349      Cost : 143.4590376924252
Iteration : 350      Cost : 143.45845753926886
Iteration : 351      Cost : 143.45787724181434
Iteration : 352      Cost : 143.45729661159984
Iteration : 353      Cost : 143.45671637961897
Iteration : 354      Cost : 143.4561365449528
Iteration : 355      Cost : 143.45555710668344
Iteration : 356      Cost : 143.45497806389403
Iteration : 357      Cost : 143.45439941566877
Iteration : 358      Cost : 143.45382116109266
Iteration : 359      Cost : 143.45324329925185
Iteration : 360      Cost : 143.45266582923352
Iteration : 361      Cost : 143.45208875012582
Iteration : 362      Cost : 143.4515120610177
Iteration : 363      Cost : 143.45093576099924
Iteration : 364      Cost : 143.4503598491616
Iteration : 365   

Iteration : 705      Cost : 143.27044372573707
Iteration : 706      Cost : 143.26995554377632
Iteration : 707      Cost : 143.26946751512912
Iteration : 708      Cost : 143.26897963891827
Iteration : 709      Cost : 143.26849191426652
Iteration : 710      Cost : 143.268004340297
Iteration : 711      Cost : 143.2675169161328
Iteration : 712      Cost : 143.26702964089714
Iteration : 713      Cost : 143.26654251371338
Iteration : 714      Cost : 143.26605553370518
Iteration : 715      Cost : 143.26556869999604
Iteration : 716      Cost : 143.26508201170978
Iteration : 717      Cost : 143.26459546797017
Iteration : 718      Cost : 143.2641090679012
Iteration : 719      Cost : 143.26362281062694
Iteration : 720      Cost : 143.2631366952715
Iteration : 721      Cost : 143.26265072095921
Iteration : 722      Cost : 143.26216488681436
Iteration : 723      Cost : 143.26167919196143
Iteration : 724      Cost : 143.26119363552493
Iteration : 725      Cost : 143.26070821662944
Iteration : 726   

Iteration : 998      Cost : 143.1302906049055
Iteration : 999      Cost : 143.12980951545882
Iteration : 1000      Cost : 143.12932831235895
Iteration : 1001      Cost : 143.128846994567
Iteration : 1002      Cost : 143.1283655610428
Iteration : 1003      Cost : 143.12788401074525
Iteration : 1004      Cost : 143.12740234263202
Iteration : 1005      Cost : 143.12692055566004
Iteration : 1006      Cost : 143.1264386487847
Iteration : 1007      Cost : 143.12595662096078
Iteration : 1008      Cost : 143.12547447114156
Iteration : 1009      Cost : 143.12499219827956
Iteration : 1010      Cost : 143.12450980132598
Iteration : 1011      Cost : 143.1240272792311
Iteration : 1012      Cost : 143.12354463094388
Iteration : 1013      Cost : 143.12306185541232
Iteration : 1014      Cost : 143.12257895158334
Iteration : 1015      Cost : 143.12209591840258
Iteration : 1016      Cost : 143.1216127548147
Iteration : 1017      Cost : 143.12112945976304
Iteration : 1018      Cost : 143.12064603219005
I

Iteration : 1184      Cost : 143.03773990937404
Iteration : 1185      Cost : 143.03721963418593
Iteration : 1186      Cost : 143.03669904478684
Iteration : 1187      Cost : 143.03617813993708
Iteration : 1188      Cost : 143.03565691839475
Iteration : 1189      Cost : 143.03513537891604
Iteration : 1190      Cost : 143.03461352025522
Iteration : 1191      Cost : 143.03409134116436
Iteration : 1192      Cost : 143.03356884039368
Iteration : 1193      Cost : 143.03304601669117
Iteration : 1194      Cost : 143.03252286880303
Iteration : 1195      Cost : 143.03199939547318
Iteration : 1196      Cost : 143.03147559544357
Iteration : 1197      Cost : 143.03095146745412
Iteration : 1198      Cost : 143.03042701024253
Iteration : 1199      Cost : 143.0299022225447
Iteration : 1200      Cost : 143.02937710309413
Iteration : 1201      Cost : 143.02885164894508
Iteration : 1202      Cost : 143.0283255661465
Iteration : 1203      Cost : 143.0277991424142
Iteration : 1204      Cost : 143.0272723764

...

Iteration : 98199      Cost : nan
Iteration : 98200      Cost : nan
Iteration : 98201      Cost : nan
Iteration : 98202      Cost : nan
Iteration : 98203      Cost : nan
Iteration : 98204      Cost : nan
Iteration : 98205      Cost : nan
Iteration : 98206      Cost : nan
Iteration : 98207      Cost : nan
Iteration : 98208      Cost : nan
Iteration : 98209      Cost : nan
Iteration : 98210      Cost : nan
Iteration : 98211      Cost : nan
Iteration : 98212      Cost : nan
Iteration : 98213      Cost : nan
Iteration : 98214      Cost : nan
Iteration : 98215      Cost : nan
Iteration : 98216      Cost : nan
Iteration : 98217      Cost : nan
Iteration : 98218      Cost : nan
Iteration : 98219      Cost : nan
Iteration : 98220      Cost : nan
Iteration : 98221      Cost : nan
Iteration : 98222      Cost : nan
Iteration : 98223      Cost : nan
Iteration : 98224      Cost : nan
Iteration : 98225      Cost : nan
Iteration : 98226      Cost : nan
Iteration : 98227      Cost : nan
Iteration : 98

Iteration : 98573      Cost : nan
Iteration : 98574      Cost : nan
Iteration : 98575      Cost : nan
Iteration : 98576      Cost : nan
Iteration : 98577      Cost : nan
Iteration : 98578      Cost : nan
Iteration : 98579      Cost : nan
Iteration : 98580      Cost : nan
Iteration : 98581      Cost : nan
Iteration : 98582      Cost : nan
Iteration : 98583      Cost : nan
Iteration : 98584      Cost : nan
Iteration : 98585      Cost : nan
Iteration : 98586      Cost : nan
Iteration : 98587      Cost : nan
Iteration : 98588      Cost : nan
Iteration : 98589      Cost : nan
Iteration : 98590      Cost : nan
Iteration : 98591      Cost : nan
Iteration : 98592      Cost : nan
Iteration : 98593      Cost : nan
Iteration : 98594      Cost : nan
Iteration : 98595      Cost : nan
Iteration : 98596      Cost : nan
Iteration : 98597      Cost : nan
Iteration : 98598      Cost : nan
Iteration : 98599      Cost : nan
Iteration : 98600      Cost : nan
Iteration : 98601      Cost : nan
Iteration : 98

Iteration : 98946      Cost : nan
Iteration : 98947      Cost : nan
Iteration : 98948      Cost : nan
Iteration : 98949      Cost : nan
Iteration : 98950      Cost : nan
Iteration : 98951      Cost : nan
Iteration : 98952      Cost : nan
Iteration : 98953      Cost : nan
Iteration : 98954      Cost : nan
Iteration : 98955      Cost : nan
Iteration : 98956      Cost : nan
Iteration : 98957      Cost : nan
Iteration : 98958      Cost : nan
Iteration : 98959      Cost : nan
Iteration : 98960      Cost : nan
Iteration : 98961      Cost : nan
Iteration : 98962      Cost : nan
Iteration : 98963      Cost : nan
Iteration : 98964      Cost : nan
Iteration : 98965      Cost : nan
Iteration : 98966      Cost : nan
Iteration : 98967      Cost : nan
Iteration : 98968      Cost : nan
Iteration : 98969      Cost : nan
Iteration : 98970      Cost : nan
Iteration : 98971      Cost : nan
Iteration : 98972      Cost : nan
Iteration : 98973      Cost : nan
Iteration : 98974      Cost : nan
Iteration : 98

Iteration : 99324      Cost : nan
Iteration : 99325      Cost : nan
Iteration : 99326      Cost : nan
Iteration : 99327      Cost : nan
Iteration : 99328      Cost : nan
Iteration : 99329      Cost : nan
Iteration : 99330      Cost : nan
Iteration : 99331      Cost : nan
Iteration : 99332      Cost : nan
Iteration : 99333      Cost : nan
Iteration : 99334      Cost : nan
Iteration : 99335      Cost : nan
Iteration : 99336      Cost : nan
Iteration : 99337      Cost : nan
Iteration : 99338      Cost : nan
Iteration : 99339      Cost : nan
Iteration : 99340      Cost : nan
Iteration : 99341      Cost : nan
Iteration : 99342      Cost : nan
Iteration : 99343      Cost : nan
Iteration : 99344      Cost : nan
Iteration : 99345      Cost : nan
Iteration : 99346      Cost : nan
Iteration : 99347      Cost : nan
Iteration : 99348      Cost : nan
Iteration : 99349      Cost : nan
Iteration : 99350      Cost : nan
Iteration : 99351      Cost : nan
Iteration : 99352      Cost : nan
Iteration : 99

Iteration : 99698      Cost : nan
Iteration : 99699      Cost : nan
Iteration : 99700      Cost : nan
Iteration : 99701      Cost : nan
Iteration : 99702      Cost : nan
Iteration : 99703      Cost : nan
Iteration : 99704      Cost : nan
Iteration : 99705      Cost : nan
Iteration : 99706      Cost : nan
Iteration : 99707      Cost : nan
Iteration : 99708      Cost : nan
Iteration : 99709      Cost : nan
Iteration : 99710      Cost : nan
Iteration : 99711      Cost : nan
Iteration : 99712      Cost : nan
Iteration : 99713      Cost : nan
Iteration : 99714      Cost : nan
Iteration : 99715      Cost : nan
Iteration : 99716      Cost : nan
Iteration : 99717      Cost : nan
Iteration : 99718      Cost : nan
Iteration : 99719      Cost : nan
Iteration : 99720      Cost : nan
Iteration : 99721      Cost : nan
Iteration : 99722      Cost : nan
Iteration : 99723      Cost : nan
Iteration : 99724      Cost : nan
Iteration : 99725      Cost : nan
Iteration : 99726      Cost : nan
Iteration : 99